In [1]:
from IPython.display import display, HTML
from bs4 import BeautifulSoup
from collections import defaultdict
from datetime import datetime, timedelta
import pandas as pd
import numpy
import requests
import re

In [2]:
CIK, SYMBOL = "0001418091", "TWTR"  # Twitter
PAGES = 5  # increase it if you want more reports
COUNT = 100  # max reports per page option
HOST = "https://www.sec.gov"
 
page_links = []
for page_n in range(PAGES):
    reports_list_url = "{}/cgi-bin/browse-edgar?action=getcompany&CIK={}&owner=include&start={}&count={}".format(
        HOST, CIK, 
        page_n * COUNT, # 0, 100, 200, ..
        COUNT
    )
    page = requests.get(reports_list_url)
    soup = BeautifulSoup(page.content, 'html.parser')

    rows = soup.find_all(string=re.compile(r'10-Q|10-K'))
    page_links.extend([r.parent.next_sibling.next_sibling.a["href"] for r in rows])

page_links

['/Archives/edgar/data/1418091/000156459018010739/0001564590-18-010739-index.htm',
 '/Archives/edgar/data/1418091/000156459018003046/0001564590-18-003046-index.htm',
 '/Archives/edgar/data/1418091/000156459017020841/0001564590-17-020841-index.htm',
 '/Archives/edgar/data/1418091/000156459017014980/0001564590-17-014980-index.htm',
 '/Archives/edgar/data/1418091/000156459017008149/0001564590-17-008149-index.htm',
 '/Archives/edgar/data/1418091/000156459017002584/0001564590-17-002584-index.htm',
 '/Archives/edgar/data/1418091/000156459016026749/0001564590-16-026749-index.htm',
 '/Archives/edgar/data/1418091/000156459016021918/0001564590-16-021918-index.htm',
 '/Archives/edgar/data/1418091/000156459016017462/0001564590-16-017462-index.htm',
 '/Archives/edgar/data/1418091/000156459016013646/0001564590-16-013646-index.htm',
 '/Archives/edgar/data/1418091/000156459015009950/0001564590-15-009950-index.htm',
 '/Archives/edgar/data/1418091/000156459015006705/0001564590-15-006705-index.htm',
 '/A

In [3]:
file_links = []

for page_link in page_links:
    page = requests.get(HOST + page_link)
    soup = BeautifulSoup(page.content, 'html.parser')
    
    # two first tables
    detail_table, report_table = soup.find_all(id="formDiv")[:2]  
    
    # get report period
    period = detail_table.find(string="Period of Report").parent.next_sibling.next_sibling.string
    
    # get report link
    file_row = report_table.find(string=re.compile(r'10-Q|10-K'))
    link = file_row.parent.next_sibling.next_sibling.a["href"]
    
    file_links.append(
        (period, link)
    )

file_links

[('2018-03-31',
  '/Archives/edgar/data/1418091/000156459018010739/twtr-10q_20180331.htm'),
 ('2017-12-31',
  '/Archives/edgar/data/1418091/000156459018003046/twtr-10k_20171231.htm'),
 ('2017-09-30',
  '/Archives/edgar/data/1418091/000156459017020841/twtr-10q_20170930.htm'),
 ('2017-06-30',
  '/Archives/edgar/data/1418091/000156459017014980/twtr-10q_20170630.htm'),
 ('2017-03-31',
  '/Archives/edgar/data/1418091/000156459017008149/twtr-10q_20170331.htm'),
 ('2016-12-31',
  '/Archives/edgar/data/1418091/000156459017002584/twtr-10k_20161231.htm'),
 ('2016-09-30',
  '/Archives/edgar/data/1418091/000156459016026749/twtr-10q_20160930.htm'),
 ('2016-06-30',
  '/Archives/edgar/data/1418091/000156459016021918/twtr-10q_20160630.htm'),
 ('2016-03-31',
  '/Archives/edgar/data/1418091/000156459016017462/twtr-10q_20160331.htm'),
 ('2015-12-31',
  '/Archives/edgar/data/1418091/000156459016013646/twtr-10k_20151231.htm'),
 ('2015-09-30',
  '/Archives/edgar/data/1418091/000156459015009950/twtr-10q_2015

In [4]:
TABLE_NAMES = ("CONSOLIDATED_BALANCE_SHEETS", 
               "CONSOLIDATED_STATEMENTS_OF_OPERATIONS", 
               "CONSOLIDATED_STATEMENTS_OF_CASH_FLOWS")

def get_numeric_value(cell):
    """
    gets number from a cell object
    """
    return int(cell.p.string.replace(",", "").replace("(", "")) * 1000

def get_value(label_cell):
    """
    gets numeric value based on a label object
    """
    current_cell = label_cell.parent.parent  # go up the tree: td > p > string
    for _ in range(3 * 2):  # go 3 columns right, *2 - because there is "\n" after each <td> element
        current_cell = current_cell.next_sibling
    return get_numeric_value(current_cell)

data = defaultdict(dict)

for period, file_link in file_links:
    page = requests.get(HOST + file_link)
    soup = BeautifulSoup(page.content, 'html.parser')
    
    shares_report = soup.find(string=re.compile(r"The number of shares of the registrant’s common stock outstanding"))
    # get 752666518 from "The number of shares of the registrant’s common stock .. was 752,666,518."
    match = re.search(r"([\d,]+)\.", shares_report)
    data["shares"][period] = int(match.group(1).replace(",", ""))
    
    for table_name in TABLE_NAMES:
        # let's find link, ex: <a name="CONSOLIDATED_BALANCE_SHEETS"> 
        table_link = soup.find("a", {"name": table_name})

        # next <div> after the link's block contains the table we are looking for
        table_html = table_link.parent.next_sibling
        while table_html.name != "div":
            table_html = table_html.next_sibling
        
        # display tables
        display(HTML("<h3>{} {}</h3>".format(table_name, period)))
        display(HTML(str(table_html)))
        
        # get data
        if table_name == "CONSOLIDATED_STATEMENTS_OF_OPERATIONS":
            # Revenue
            revenue_label = table_html.find(string="Revenue")
            data["raw_revenue"][period] = get_value(revenue_label) 
            
            # Cost of Revenue
            cost_of_revenue_label = table_html.find(string="Cost of revenue")
            data["raw_cost_of_revenue"][period] = get_value(cost_of_revenue_label)
            
            
            # Net income (loss)
            net_income_label = table_html.find(string="Net income (loss)")
            if net_income_label is None:  # lable string is different for the year report
                net_income_label = table_html.find(string="Net loss")
            data["net_income"][period] = get_value(net_income_label) * -1
            
        elif table_name == "CONSOLIDATED_BALANCE_SHEETS":
            # Convertible notes
            convertible_notes_label = table_html.find(string="Convertible notes")
            data["convertible_notes"][period] = get_value(convertible_notes_label)
            
            # Total stockholders' equity
            equity_label = table_html.find(string="Total stockholders' equity")
            data["equity"][period] = get_value(equity_label)

In [5]:
df = pd.DataFrame.from_records(data)

df

convertible_notes      equity  net_income  raw_cost_of_revenue  \
2014-09-30         1293604000  3525038000  -175464000            124166000   
2014-12-31         1376020000  3626403000  -577820000            446309000   
2015-03-31         1395113000  3687097000  -162442000            143475000   
2015-06-30         1414896000  4231184000  -136663000            167623000   
2015-09-30         1434968000  4274163000  -131690000            200195000   
2015-12-31         1455095000  4368047000  -521031000            729256000   
2016-03-31         1475513000  4477486000   -79731000            198405000   
2016-06-30         1496440000  4556853000  -107217000            202966000   
2016-09-30         1517673000  4629332000  -102871000            225159000   
2016-12-31         1538967000  4604935000  -456873000            932240000   
2017-03-31         1560330000  4690376000   -61559000            220339000   
2017-06-30         1582468000  4728896000  -116488000            212908000   
2017-09-30         1604932000  4829406000   -21095000            210016000   
2017-12-31         1627460000  5047218000  -108063000            861242000   
2018-03-31         1650064000  5210436000   -60997000            222823000   

            raw_revenue     shares  
2014-09-30    361266000  634511461  
2014-12-31   1403002000  647836523  
2015-03-31    435939000  654774147  
2015-06-30    502383000  676304418  
2015-09-30    569237000  682946653  
2015-12-31   2218032000  697726321  
2016-03-31    594521000  701897432  
2016-06-30    601958000  707726943  
2016-09-30    615934000  714902970  
2016-12-31   2529619000  726894203  
2017-03-31    548251000  730833073  
2017-06-30    573855000  737893225  
2017-09-30    589633000  742793573  
2017-12-31   2443299000  750904551  
2018-03-31    664871000  752666518

In [6]:
# Important: companies report 3 quarterly reports while the 4th report is the annual one. 
# We want to show in our table data for the year but also for all 4 quarters. 
# We’ll have to do very basic math to calculate Q4 data.
df["sum_3q_revenue"] = df.raw_revenue.rolling(window=3).sum()
df["revenue"] = df.raw_revenue.where(
    ~df.index.to_series().str.contains("-12-"), # if month is not 12 then revenue is OK else
    other=df.raw_revenue - df.sum_3q_revenue.shift()  # total minus sum of revenues from prev 3 reports
)

df[["raw_revenue", "sum_3q_revenue", "revenue"]]

raw_revenue  sum_3q_revenue      revenue
2014-09-30    361266000             NaN  361266000.0
2014-12-31   1403002000             NaN          NaN
2015-03-31    435939000    2.200207e+09  435939000.0
2015-06-30    502383000    2.341324e+09  502383000.0
2015-09-30    569237000    1.507559e+09  569237000.0
2015-12-31   2218032000    3.289652e+09  710473000.0
2016-03-31    594521000    3.381790e+09  594521000.0
2016-06-30    601958000    3.414511e+09  601958000.0
2016-09-30    615934000    1.812413e+09  615934000.0
2016-12-31   2529619000    3.747511e+09  717206000.0
2017-03-31    548251000    3.693804e+09  548251000.0
2017-06-30    573855000    3.651725e+09  573855000.0
2017-09-30    589633000    1.711739e+09  589633000.0
2017-12-31   2443299000    3.606787e+09  731560000.0
2018-03-31    664871000    3.697803e+09  664871000.0

In [7]:
# then normalize cost_of_revenue
df["sum_3q_cost_of_revenue"] = df.raw_cost_of_revenue.rolling(window=3).sum()
df["cost_of_revenue"] = df.raw_cost_of_revenue.where(
    ~df.index.to_series().str.contains("-12-"), # if month is not 12 then revenue is OK else
    other=df.raw_cost_of_revenue - df.sum_3q_cost_of_revenue.shift()  # total minus sum of revenues from prev 3 reports
)

df[["raw_cost_of_revenue", "sum_3q_cost_of_revenue", "cost_of_revenue"]]

raw_cost_of_revenue  sum_3q_cost_of_revenue  cost_of_revenue
2014-09-30            124166000                     NaN      124166000.0
2014-12-31            446309000                     NaN              NaN
2015-03-31            143475000            7.139500e+08      143475000.0
2015-06-30            167623000            7.574070e+08      167623000.0
2015-09-30            200195000            5.112930e+08      200195000.0
2015-12-31            729256000            1.097074e+09      217963000.0
2016-03-31            198405000            1.127856e+09      198405000.0
2016-06-30            202966000            1.130627e+09      202966000.0
2016-09-30            225159000            6.265300e+08      225159000.0
2016-12-31            932240000            1.360365e+09      305710000.0
2017-03-31            220339000            1.377738e+09      220339000.0
2017-06-30            212908000            1.365487e+09      212908000.0
2017-09-30            210016000            6.432630e+08      210016000.0
2017-12-31            861242000            1.284166e+09      217979000.0
2018-03-31            222823000            1.294081e+09      222823000.0

In [8]:
# Metric 1: Gross Margin %
# Revenues – 589m
# Cost of revenue – 210m
# Gross profit = 379m (589m – 210m)
# Gross margin = 64% (379/589)

df["gross_profit"] = df.revenue - df.cost_of_revenue
df["gross_margin"] = df.gross_profit / df.revenue * 100

df[["revenue", "cost_of_revenue", "gross_profit", "gross_margin"]]

revenue  cost_of_revenue  gross_profit  gross_margin
2014-09-30  361266000.0      124166000.0   237100000.0     65.630311
2014-12-31          NaN              NaN           NaN           NaN
2015-03-31  435939000.0      143475000.0   292464000.0     67.088285
2015-06-30  502383000.0      167623000.0   334760000.0     66.634420
2015-09-30  569237000.0      200195000.0   369042000.0     64.830993
2015-12-31  710473000.0      217963000.0   492510000.0     69.321424
2016-03-31  594521000.0      198405000.0   396116000.0     66.627756
2016-06-30  601958000.0      202966000.0   398992000.0     66.282365
2016-09-30  615934000.0      225159000.0   390775000.0     63.444298
2016-12-31  717206000.0      305710000.0   411496000.0     57.374869
2017-03-31  548251000.0      220339000.0   327912000.0     59.810561
2017-06-30  573855000.0      212908000.0   360947000.0     62.898642
2017-09-30  589633000.0      210016000.0   379617000.0     64.381912
2017-12-31  731560000.0      217979000.0   513581000.0     70.203538
2018-03-31  664871000.0      222823000.0   442048000.0     66.486281

In [9]:
# Metric 2: Net Margin %
# Revenues – 589m
# Net income – -21m
# Net margin = -4% (-21m/589m)

df["net_margin"] = df.net_income / df.revenue * 100


df[["net_income", "revenue", "net_margin"]]

net_income      revenue  net_margin
2014-09-30  -175464000  361266000.0  -48.569198
2014-12-31  -577820000          NaN         NaN
2015-03-31  -162442000  435939000.0  -37.262553
2015-06-30  -136663000  502383000.0  -27.202951
2015-09-30  -131690000  569237000.0  -23.134477
2015-12-31  -521031000  710473000.0  -73.335792
2016-03-31   -79731000  594521000.0  -13.410964
2016-06-30  -107217000  601958000.0  -17.811376
2016-09-30  -102871000  615934000.0  -16.701627
2016-12-31  -456873000  717206000.0  -63.701782
2017-03-31   -61559000  548251000.0  -11.228251
2017-06-30  -116488000  573855000.0  -20.299205
2017-09-30   -21095000  589633000.0   -3.577649
2017-12-31  -108063000  731560000.0  -14.771584
2018-03-31   -60997000  664871000.0   -9.174261

In [10]:
# Metric 3: Debt to Equity
# Debt (Convertible Notes) – 1600m
# Equity -  4800m
# Debt / Equity = .33

df["debt_to_equity"] = df.convertible_notes / df.equity


df[["convertible_notes", "equity", "debt_to_equity"]]

convertible_notes      equity  debt_to_equity
2014-09-30         1293604000  3525038000        0.366976
2014-12-31         1376020000  3626403000        0.379445
2015-03-31         1395113000  3687097000        0.378377
2015-06-30         1414896000  4231184000        0.334397
2015-09-30         1434968000  4274163000        0.335731
2015-12-31         1455095000  4368047000        0.333123
2016-03-31         1475513000  4477486000        0.329541
2016-06-30         1496440000  4556853000        0.328393
2016-09-30         1517673000  4629332000        0.327838
2016-12-31         1538967000  4604935000        0.334200
2017-03-31         1560330000  4690376000        0.332666
2017-06-30         1582468000  4728896000        0.334638
2017-09-30         1604932000  4829406000        0.332325
2017-12-31         1627460000  5047218000        0.322447
2018-03-31         1650064000  5210436000        0.316684

In [11]:
# Metric 4: PE ratio:
# Total Net Profit for the last 4 quarters
# Market cap = total shares x today’s stock price
# PE ratio = Total Net Profit / Market cap

# get today's price
url = "https://query1.finance.yahoo.com/v7/finance/options/{}".format(SYMBOL)
page = requests.get(url)
response = page.json()    
df["price"] = response['optionChain']['result'][0]['quote']['regularMarketPrice']

df["net_income_for_4q"] = df.net_income.rolling(window=4).sum()
df["market_cap"] = df.shares * df.price
df["PE_ratio"] = df.net_income_for_4q / df.market_cap


df[["net_income", "net_income_for_4q", "shares", "price", "market_cap", "PE_ratio"]]

net_income  net_income_for_4q     shares  price    market_cap  \
2014-09-30  -175464000                NaN  634511461  41.21  2.614822e+10   
2014-12-31  -577820000                NaN  647836523  41.21  2.669734e+10   
2015-03-31  -162442000                NaN  654774147  41.21  2.698324e+10   
2015-06-30  -136663000      -1.052389e+09  676304418  41.21  2.787051e+10   
2015-09-30  -131690000      -1.008615e+09  682946653  41.21  2.814423e+10   
2015-12-31  -521031000      -9.518260e+08  697726321  41.21  2.875330e+10   
2016-03-31   -79731000      -8.691150e+08  701897432  41.21  2.892519e+10   
2016-06-30  -107217000      -8.396690e+08  707726943  41.21  2.916543e+10   
2016-09-30  -102871000      -8.108500e+08  714902970  41.21  2.946115e+10   
2016-12-31  -456873000      -7.466920e+08  726894203  41.21  2.995531e+10   
2017-03-31   -61559000      -7.285200e+08  730833073  41.21  3.011763e+10   
2017-06-30  -116488000      -7.377910e+08  737893225  41.21  3.040858e+10   
2017-09-30   -21095000      -6.560150e+08  742793573  41.21  3.061052e+10   
2017-12-31  -108063000      -3.072050e+08  750904551  41.21  3.094478e+10   
2018-03-31   -60997000      -3.066430e+08  752666518  41.21  3.101739e+10   

            PE_ratio  
2014-09-30       NaN  
2014-12-31       NaN  
2015-03-31       NaN  
2015-06-30 -0.037760  
2015-09-30 -0.035837  
2015-12-31 -0.033103  
2016-03-31 -0.030047  
2016-06-30 -0.028790  
2016-09-30 -0.027523  
2016-12-31 -0.024927  
2017-03-31 -0.024189  
2017-06-30 -0.024263  
2017-09-30 -0.021431  
2017-12-31 -0.009928  
2018-03-31 -0.009886

In [12]:
# Metric 5: Revenue growth y/y
# Revenue growth for a quarter vs last year quarter
# Average growth 
df["revenue_year"] = df.revenue - df.revenue.shift(periods=4)
df["avg_revenue_year"] = df.revenue_year.rolling(window=100, min_periods=1).mean()

df[["revenue", "revenue_year", "avg_revenue_year"]]

revenue  revenue_year  avg_revenue_year
2014-09-30  361266000.0           NaN               NaN
2014-12-31          NaN           NaN               NaN
2015-03-31  435939000.0           NaN               NaN
2015-06-30  502383000.0           NaN               NaN
2015-09-30  569237000.0   207971000.0      2.079710e+08
2015-12-31  710473000.0           NaN      2.079710e+08
2016-03-31  594521000.0   158582000.0      1.832765e+08
2016-06-30  601958000.0    99575000.0      1.553760e+08
2016-09-30  615934000.0    46697000.0      1.282062e+08
2016-12-31  717206000.0     6733000.0      1.039116e+08
2017-03-31  548251000.0   -46270000.0      7.888133e+07
2017-06-30  573855000.0   -28103000.0      6.359786e+07
2017-09-30  589633000.0   -26301000.0      5.236050e+07
2017-12-31  731560000.0    14354000.0      4.813756e+07
2018-03-31  664871000.0   116620000.0      5.498580e+07

In [13]:
# Metric 6: Revenue growth q/q
# Revenue growth for a quarter to quarter
# Average growth
df["revenue_quarter"] = df.revenue - df.revenue.shift()
df["avg_revenue_quarter"] = df.revenue_quarter.rolling(window=100, min_periods=1).mean()

df[["revenue", "revenue_quarter", "avg_revenue_quarter"]]

revenue  revenue_quarter  avg_revenue_quarter
2014-09-30  361266000.0              NaN                  NaN
2014-12-31          NaN              NaN                  NaN
2015-03-31  435939000.0              NaN                  NaN
2015-06-30  502383000.0       66444000.0         6.644400e+07
2015-09-30  569237000.0       66854000.0         6.664900e+07
2015-12-31  710473000.0      141236000.0         9.151133e+07
2016-03-31  594521000.0     -115952000.0         3.964550e+07
2016-06-30  601958000.0        7437000.0         3.320380e+07
2016-09-30  615934000.0       13976000.0         2.999917e+07
2016-12-31  717206000.0      101272000.0         4.018100e+07
2017-03-31  548251000.0     -168955000.0         1.403900e+07
2017-06-30  573855000.0       25604000.0         1.532400e+07
2017-09-30  589633000.0       15778000.0         1.536940e+07
2017-12-31  731560000.0      141927000.0         2.687464e+07
2018-03-31  664871000.0      -66689000.0         1.907767e+07

In [14]:
# Metric 7: Revenue per share
# Revenue – 589m
# Number of shares – 752m
# Revenue per share = $0.78
df["revenue_per_share"] = df.revenue / df.shares

df[["revenue", "shares", "revenue_per_share"]]

revenue     shares  revenue_per_share
2014-09-30  361266000.0  634511461           0.569361
2014-12-31          NaN  647836523                NaN
2015-03-31  435939000.0  654774147           0.665785
2015-06-30  502383000.0  676304418           0.742836
2015-09-30  569237000.0  682946653           0.833501
2015-12-31  710473000.0  697726321           1.018269
2016-03-31  594521000.0  701897432           0.847020
2016-06-30  601958000.0  707726943           0.850551
2016-09-30  615934000.0  714902970           0.861563
2016-12-31  717206000.0  726894203           0.986672
2017-03-31  548251000.0  730833073           0.750173
2017-06-30  573855000.0  737893225           0.777694
2017-09-30  589633000.0  742793573           0.793805
2017-12-31  731560000.0  750904551           0.974238
2018-03-31  664871000.0  752666518           0.883354

In [15]:
# Charts with plotly
import plotly.graph_objs as plotly_go
import plotly
plotly.tools.set_credentials_file(username='aleksey.stryukov', api_key='BfBbOOQRaHVZEbRYrbtm')

In [16]:
data = [plotly_go.Scatter(x=df.index, y=df.revenue, name='Revenue'), 
        plotly_go.Scatter(x=df.index, y=df.net_margin, name='Net Profit Margin', yaxis='y2')]

layout = plotly_go.Layout(
    title="Revenue and Net Profit Margin (quarterly)",
    yaxis=dict(
        title='Revenue'
    ),
    yaxis2=dict(
        title='Net Profit Margin, %',
        overlaying='y',
        side='right'
    ),
)

fig = plotly_go.Figure(data=data, layout=layout)
plotly.plotly.iplot(fig, filename='17-1')

In [17]:
data = [plotly_go.Scatter(x=df.index, y=df.revenue, name='Revenue'), 
        plotly_go.Scatter(x=df.index, y=df.revenue_year, name='Revenue Growth Y/Y', yaxis='y2')]

layout = plotly_go.Layout(
    title="Revenue and Revenue Growth Y/Y (quarterly)",
    yaxis=dict(
        title='Revenue'
    ),
    yaxis2=dict(
        title='Revenue Growth Y/Y',
        overlaying='y',
        side='right'
    ),
)

fig = plotly_go.Figure(data=data, layout=layout)
plotly.plotly.iplot(fig, filename='17-2')

In [18]:
data = [plotly_go.Scatter(x=df.index, y=df.convertible_notes, name='Debt'), 
        plotly_go.Scatter(x=df.index, y=df.debt_to_equity, name='Debt-Equity ratio', yaxis='y2')]

layout = plotly_go.Layout(
    title="Debt and Debt-Equity ratio (quarterly)",
    yaxis=dict(
        title='Debt'
    ),
    yaxis2=dict(
        title='Debt-Equity ratio',
        overlaying='y',
        side='right'
    ),
)

fig = plotly_go.Figure(data=data, layout=layout)
plotly.plotly.iplot(fig, filename='17-3')

In [19]:
# get share prices for the period 
start = datetime.strptime(df.index.min(), "%Y-%m-%d")
end = datetime.strptime(df.index.max(), "%Y-%m-%d") + timedelta(days=1)
url = "https://query1.finance.yahoo.com/v8/finance/chart/{symbol}?"\
      "symbol={symbol}&period1={start}&period2={end}&interval=1d".format(
          symbol=SYMBOL,
          start=int(start.timestamp()),
          end=int(end.timestamp()),
      )
    
page = requests.get(url)
data = page.json()['chart']['result'][0]
quote = data['indicators']['quote'][0]

share_prices = pd.DataFrame(
        index=pd.Index(data=[datetime.fromtimestamp(t).date() for t in data['timestamp']], name="Date"),
        data=dict(
            Open=quote["open"],
            High=quote["high"],
            Low=quote["low"],
            Close=quote["close"],
            Volume=quote["volume"],
        )
    ) 

share_prices

Close       High        Low       Open    Volume
Date                                                            
2014-09-30  51.580002  52.189999  51.169998  52.000000  12315700
2014-10-01  50.060001  51.290001  49.150002  51.080002  24733500
2014-10-02  51.849998  52.099998  50.009998  51.029999  27056500
2014-10-03  53.939999  54.730000  52.110001  52.750000  31227200
2014-10-06  53.490002  54.450001  53.230000  53.939999  20033400
2014-10-07  53.529999  54.990002  53.099998  53.119999  26082300
2014-10-08  55.419998  55.669998  52.599998  53.619999  31098500
2014-10-09  55.290001  55.990002  54.919998  55.290001  29741400
2014-10-10  50.400002  55.660000  50.299999  54.570000  46727300
2014-10-13  48.490002  51.910000  48.259998  50.540001  35326800
2014-10-14  48.580002  49.529999  47.080002  49.060001  29723600
2014-10-15  49.990002  50.520000  46.380001  47.110001  34371500
2014-10-16  48.230000  49.820000  47.169998  48.340000  30818800
2014-10-17  48.770000  50.250000  48.650002  49.720001  24630600
2014-10-20  50.700001  50.889999  48.799999  49.070000  17781100
2014-10-21  50.630001  52.150002  50.299999  51.759998  21351000
2014-10-22  49.080002  51.840000  49.000000  51.130001  26147900
2014-10-23  49.669998  50.400002  49.200001  50.130001  23099800
2014-10-24  49.950001  50.189999  49.150002  50.160000  12035200
2014-10-27  48.560001  50.240002  47.180000  50.020000  51896300
2014-10-28  43.779999  44.580002  41.759998  42.250000  83514000
2014-10-29  42.080002  44.160000  41.810001  43.849998  40261900
2014-10-30  41.799999  42.480000  39.939999  41.560001  42012600
2014-10-31  41.470001  42.849998  41.340000  42.689999  23895100
2014-11-03  40.209999  41.200001  40.160000  40.549999  31441900
2014-11-04  40.900002  41.099998  39.750000  40.029999  19544300
2014-11-05  40.369999  41.799999  40.130001  41.689999  19742200
2014-11-06  40.840000  41.349998  40.099998  40.189999  16292100
2014-11-07  40.310001  40.740002  39.700001  40.740002  18558900
2014-11-10  39.590000  40.689999  39.419998  40.340000  19069300
...               ...        ...        ...        ...       ...
2018-02-15  33.610001  34.380001  33.060001  34.029999  32020500
2018-02-16  33.060001  33.500000  32.680000  33.369999  27901000
2018-02-20  32.840000  33.570000  32.680000  32.880001  22766700
2018-02-21  33.380001  34.060001  32.650002  33.029999  29589300
2018-02-22  32.110001  33.450001  31.629999  33.430000  29184100
2018-02-23  32.660000  32.689999  31.969999  32.200001  17283400
2018-02-26  32.160000  32.700001  31.959999  32.700001  15766300
2018-02-27  31.320000  32.209999  31.260000  31.910000  16544000
2018-02-28  31.860001  32.849998  31.469999  31.500000  24180100
2018-03-01  32.240002  32.560001  31.260000  31.950001  25032500
2018-03-02  33.000000  33.029999  31.490000  31.930000  24918900
2018-03-05  34.580002  34.950001  32.580002  32.900002  34840000
2018-03-06  34.430000  34.950001  33.860001  34.580002  22641000
2018-03-07  35.759998  35.820000  33.990002  33.990002  33656100
2018-03-08  34.849998  35.840000  34.680000  35.419998  24845300
2018-03-09  35.349998  35.500000  34.939999  35.200001  19119500
2018-03-12  35.500000  35.730000  34.830002  35.529999  21078900
2018-03-13  34.110001  35.529999  33.900002  35.400002  22096900
2018-03-14  36.599998  36.799999  34.090000  34.299999  41632800
2018-03-15  35.799999  36.480000  35.400002  36.410000  20921800
2018-03-16  35.580002  36.200001  35.520000  36.000000  13833800
2018-03-19  34.980000  35.740002  34.410000  35.130001  22194800
2018-03-20  31.350000  34.950001  30.610001  34.919998  82937600
2018-03-21  32.730000  33.150002  32.049999  32.189999  43672100
2018-03-22  31.200001  32.130001  31.180000  31.770000  29561900
2018-03-23  31.030001  32.000000  30.790001  31.260000  24878100
2018-03-26  31.910000  32.470001  30.700001  31.690001  25546300
2018-03-27  28.070000  31.900000  27.879999  31.850000  80415500
2018-03-28  28.450001  29.110001  27.389999  27.780

In [20]:
candlestick = plotly_go.Candlestick(
    x=share_prices.index,
    open=share_prices.Open,
    high=share_prices.High,
    low=share_prices.Low,
    close=share_prices.Close,
    name="Share Price"
)
revenue = plotly_go.Scatter(x=df.index, y=df.revenue, name='Revenue', yaxis='y2')
data = [candlestick, revenue]
layout = plotly_go.Layout(
    title="Share price (daily) and Revenues (quarterly)",
    yaxis=dict(
        title='Share price'
    ),
    yaxis2=dict(
        title='Revenue',
        overlaying='y',
        side='right'
    ),
)

fig = plotly_go.Figure(data=data, layout=layout)
plotly.plotly.iplot(fig, filename='17-4')